# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [35 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [3]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [4]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.15
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.15', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.15\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [5]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [6]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7eff17821350>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 35
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 35, 'EVs_n_max': 1827, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [7]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
#env.plot_VPP_input_data()

Charging event: 1, Arrival time: 2022-01-01 06:45:00, Parking_time: 24, Leaving_time: 2022-01-02 06:45:00, SOC: 0.4288450632398552, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 1825, Arrival time: 2022-12-31 08:45:00, Parking_time: 24, Leaving_time: 2023-01-01 08:45:00, SOC: 0.5152456379745263, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en(grid-import)=4947.18kWh , autarky-rate=83.0 , RE-to-vehicle_unused_en(grid-export)=-26161.81kWh , self-consump.rate=47.9 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  34308.26 , Grid_used_en=kWh  49140.39 , RE-to-vehicle_unused_en=kWh  14832.13 , Total_selling_cost=€  1280.82 , Grid_cost=€  1707.18 , Charging_events=  1825 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  64.34


In [8]:
env.plot_ELVIS_data()

In [9]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  35559.74 , Grid_used_en(grid-import)=50203.59kWh , Total_demand=85820.42kWh , autarky-rate=41.5 , RE-to-vehicle_unused_en(grid-export)=14643.85kWh , Total_supply=50260.68kWh , self-consump.rate=70.9 , Grid_cost=€  1750.25 , Total_selling_cost=€  1311.89 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  64.34
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [10]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_autarky()

In [12]:
#env.plot_Elvis_results()

In [13]:
#env.plot_VPP_results()

In [14]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_VPP_Elvis_comparison()

In [16]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [17]:
#env.plot_rewards_stats()

In [18]:
env.plot_EVs_kpi()

In [19]:
env.plot_actions_kpi()

In [20]:
env.plot_load_kpi()

In [21]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [22]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [23]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [24]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
#VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')
VPP_table = env.VPP_table

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  35292.64 , Grid_used_en(grid-import)=50727.03kWh , Total_demand=85558.45kWh , autarky-rate=40.7 , RE-to-vehicle_unused_en(grid-export)=15434.39kWh , Total_supply=50265.81kWh , self-consump.rate=69.3 , Grid_cost=€  1778.11 , Total_selling_cost=€  1325.09 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  64.34
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -673.58 , Grid_used_en(grid-import)=1295.28kWh , Total_demand=66129.46kWh , autarky-rate=98.0 , RE-to-vehicle_unused_en(grid-export)=1968.86kWh , Total_supply=66803.04kWh , self-consump.rate=97.1 , Total_selling_cost=€  5.28 , Grid_cost=€  48.78 
 EV_INFO: Av.EV_energy_leaving=kWh  61.14 , Std.EV_energy_leaving=kWh  23.77 , EV_departures =  1825 , EV_queue_left =  0
SCORE:  Cumulative_reward= 489151.74 - Step_rewars (load_t= 455708.48, EVs_ene

In [25]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [26]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  64.966400  48.755985  48.663933  50.654346   
2022-01-01 00:15:00  65.216400  48.172874  48.080822  50.904346   
2022-01-01 00:30:00  65.466400  47.715397  47.623344  51.154346   
2022-01-01 00:45:00  65.716400  47.353912  47.261860  51.404346   
2022-01-01 01:00:00  65.966400  46.843143  46.751091  51.654346   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  90.836700  35.282742  73.429253  66.586136   
2022-06-06 05:00:00  90.836700  35.032742  75.096375  68.253258   
2022-06-06 05:15:00  91.769714  35.032742  76.029388  69.186272   
2022-06-06 05:30:00  92.834312  34.782742  77.093987  70.250870   
2022-06-06 05:45:00  93.905365  34.532742  78.165039  71.321922   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [5471, 5469, 5470, 5472]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [5471, 5469, 5470, 5472]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [5471, 5469, 5470, 5472]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [5471, 5469, 5470, 5472]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [6273, 6274, 6275, 6276]  [0, 2, 1, 1]   
2022-06-06 05:00:00  [6273, 6274, 6275, 6276]  [1, 0, 1, 1]   
2022-06-06 05:15:00  [6273, 6274, 6275, 6276]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [6273, 6274, 6275, 6276]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [6273, 6274, 6275, 6276]  [1, 2, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00     [True, False, True, True]       10.163604   
2022-06-06 05:00:00     [True, False, True, True]       13.336982   
2022-06-06 05:15:00    [False, False, True, True]       11.196143   
2022-06-06 05:30:00    [False, False, True, True]       12.775159   
2022-06-06 05:45:00    [False, False, True, True]       12.852604   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00           0.000000  1.264482         15.0        0.0   
2022-01-01 00:15:00          -4.664895  0.000000         15.0        0.0   
2022-01-01 00:30:00          -3.659806  0.000000         15.0        0.0   
2022-01-01 00:45:00          -2.891884  0.000000         15.0        0.0   
2022-01-01 01:00:00          -4.086154  0.000000         15.0        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00          -1.000000  0.000000         15.0        0.0   
2022-06-06 05:00:00          -1.000000  0.000000         15.0        0.0   
2022-06-06 05:15:00           0.000000  0.000000         15.0        0.0   
2022-06-06 05:30:00          -1.000000  0.000000         15.0        0.0   
2022-06-06 05:45:00          -1.000000  0.000000         15.0        0.0   

                     rewards  
time                          
2022-01-01 00:00:00     15.0  
2022-01-01 00:15:00     15.0  
2022-01-01 00:30:00     15.0  
2022-01-01 00:45:00     15.0  
2022-01-01 01:00:00     15.0  
...                      ...  
2022-06-06 04:45:00     15.0  
2022-06-06 05:00:00     15.0  
2022-06-06 05:15:00     15.0  
2022-06-06 05:30:00     15.0  
2022-06-06 05:45:00     15.0  

[15000 rows x 13 columns]

In [27]:
env.plot_VPP_autarky()

In [28]:
#env.plot_Elvis_results()

In [29]:
#env.plot_VPP_results()

In [30]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [31]:
env.plot_VPP_Elvis_comparison()

In [32]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [33]:
env.plot_rewards_stats()

In [34]:
env.plot_EVs_kpi()

In [35]:
env.plot_load_kpi()

In [36]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [37]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7301, Arrival time: 2022-01-01 01:45:00, Parking_time: 23.287691317668934, Leaving_time: 2022-01-02 01:02:15.688744, SOC: 0.4444437340816576, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 9125, Arrival time: 2022-12-31 18:15:00, Parking_time: 23.313791356859035, Leaving_time: 2023-01-01 17:33:49.648885, SOC: 0.4753010391772046, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en(grid-import)=2136.67kWh , autarky-rate=89.6 , RE-to-vehicle_unused_en(grid-export)=-32222.06kWh , self-consump.rate=36.4 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  25990.3 , Grid_used_en=kWh  45703.77 , RE-to-vehicle_unused_en=kWh  19713.47 , Total_selling_cost=€  1177.97 , Grid_cost=€  1989.95 , Charging_events=  1825 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  67.66


In [38]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  25377.46 , Grid_used_en(grid-import)=45018.99kWh , Total_demand=76009.7kWh , autarky-rate=40.8 , RE-to-vehicle_unused_en(grid-export)=19641.52kWh , Total_supply=50632.24kWh , self-consump.rate=61.2 , Grid_cost=€  1984.28 , Total_selling_cost=€  1185.23 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  67.66
Simulating VPP....


In [39]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [40]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  25535.9 , Grid_used_en(grid-import)=45327.0kWh , Total_demand=76154.65kWh , autarky-rate=40.5 , RE-to-vehicle_unused_en(grid-export)=19791.11kWh , Total_supply=50618.75kWh , self-consump.rate=60.9 , Grid_cost=€  1985.66 , Total_selling_cost=€  1186.17 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  67.66
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2777.18 , Grid_used_en(grid-import)=451.06kWh , Total_demand=61445.22kWh , autarky-rate=99.3 , RE-to-vehicle_unused_en(grid-export)=3228.24kWh , Total_supply=64222.4kWh , self-consump.rate=95.0 , Total_selling_cost=€  -96.66 , Grid_cost=€  18.59 
 EV_INFO: Av.EV_energy_leaving=kWh  65.16 , Std.EV_energy_leaving=kWh  23.65 , EV_departures =  1818 , EV_queue_left =  3
SCORE:  Cumulative_reward= 515428.11 - Step_rewars (load_t= 445237.32, EVs_ener

In [41]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  90.873245  57.024021  56.048668  79.373169   
2022-06-06 05:00:00  91.770821  57.921597  56.946243  80.270744   
2022-06-06 05:15:00  92.711609  58.862385  57.887032  81.211533   
2022-06-06 05:30:00  93.521492  59.672268  58.696915  82.021416   
2022-06-06 05:45:00  94.371803  60.522583  59.547230  82.871727   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 04:45:00  [11749, 11752, 11750, 11751]  [1, 1, 1, 1]   
2022-06-06 05:00:00  [11749, 11752, 11750, 11751]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [11749, 11752, 11750, 11751]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [11749, 11752, 11750, 11751]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [11749, 11752, 11750, 11751]  [1, 1, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00     [True, True, True, True]       10.601875   
2022-06-06 05:00:00    [False, True, True, True]       14.361195   
2022-06-06 05:15:00    [False, True, True, True]       15.052623   
2022-06-06 05:30:00    [False, True, True, True]       12.958125   
2022-06-06 05:45:00    [False, True, True, True]       13.605015   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -4.591654    -3.985449        0.0   
2022-01-01 00:15:00                0.0 -3.391270    -4.453069        0.0   
2022-01-01 00:30:00                0.0 -3.671842    -3.766620        0.0   
2022-01-01 00:45:00                0.0 -3.259972    -4.322778        0.0   
2022-01-01 01:00:00                0.0 -3.593667    -5.383713        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:00:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:15:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:30:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:45:00                0.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -3.985449  
2022-01-01 00:15:00  -4.453069  
2022-01-01 00:30:00  -3.766620  
2022-01-01 00:45:00  -4.322778  
2022-01-01 01:00:00  -5.383713  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:4

In [43]:
env.plot_VPP_autarky()

In [44]:
#env.plot_VPP_results()


In [45]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [46]:
env.plot_VPP_Elvis_comparison()

In [47]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [48]:
env.plot_rewards_stats()

In [49]:
env.plot_EVs_kpi()

In [50]:
env.plot_load_kpi()

In [51]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [52]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 12776, Arrival time: 2022-01-01 07:45:00, Parking_time: 24, Leaving_time: 2022-01-02 07:45:00, SOC: 0.39843605702555795, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 14600, Arrival time: 2022-12-31 19:00:00, Parking_time: 24, Leaving_time: 2023-01-01 19:00:00, SOC: 0.4984481086594103, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en(grid-import)=1556.25kWh , autarky-rate=90.5 , RE-to-vehicle_unused_en(grid-export)=-35673.95kWh , self-consump.rate=29.4 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22890.94 , Grid_used_en=kWh  43092.43 , RE-to-vehicle_unused_en=kWh  20201.49 , Total_selling_cost=€  1035.82 , Grid_cost=€  1779.91 , Charging_events=  1825 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  69.55


In [53]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21204.9 , Grid_used_en(grid-import)=42604.34kWh , Total_demand=71672.88kWh , autarky-rate=40.6 , RE-to-vehicle_unused_en(grid-export)=21399.44kWh , Total_supply=50467.98kWh , self-consump.rate=57.6 , Grid_cost=€  1771.89 , Total_selling_cost=€  990.54 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  69.55
Simulating VPP....


In [54]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [55]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21989.36 , Grid_used_en(grid-import)=42608.54kWh , Total_demand=72498.88kWh , autarky-rate=41.2 , RE-to-vehicle_unused_en(grid-export)=20619.18kWh , Total_supply=50509.52kWh , self-consump.rate=59.2 , Grid_cost=€  1781.94 , Total_selling_cost=€  1015.42 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  69.55
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3228.46 , Grid_used_en(grid-import)=496.39kWh , Total_demand=59997.83kWh , autarky-rate=99.2 , RE-to-vehicle_unused_en(grid-export)=3724.86kWh , Total_supply=63226.3kWh , self-consump.rate=94.1 , Total_selling_cost=€  -102.43 , Grid_cost=€  20.42 
 EV_INFO: Av.EV_energy_leaving=kWh  66.71 , Std.EV_energy_leaving=kWh  22.55 , EV_departures =  1824 , EV_queue_left =  0
SCORE:  Cumulative_reward= 520277.97 - Step_rewars (load_t= 436103.24, EVs_e

In [56]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [57]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  51.894413   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  91.251648  51.911076  23.951805  90.906387   
2022-06-06 03:45:00  92.026588  51.661076  23.701805  91.681328   
2022-06-06 04:00:00  93.093010  51.411076  23.451805  92.747749   
2022-06-06 04:15:00  94.195648  51.161076  23.201805  93.850388   
2022-06-06 04:30:00  95.275948  50.911076  22.951805  94.930687   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [1, 0, 0, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 0, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
...                                           ...           ...   
2022-06-06 03:30:00  [17258, 17257, 17260, 17259]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [17258, 17257, 17260, 17259]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [17258, 17257, 17260, 17259]  [1, 2, 2, 1]   
2022-06-06 04:15:00  [17258, 17257, 17260, 17259]  [1, 2, 2, 1]   
2022-06-06 04:30:00  [17258, 17257, 17260, 17259]  [1, 1, 2, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00     [False, True, True, True]        0.000000   
2022-01-01 00:15:00    [False, False, True, True]        3.158331   
2022-01-01 00:30:00   [False, False, False, True]        0.000000   
2022-01-01 00:45:00   [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, False, False, True]        0.000000   
...                                           ...             ...   
2022-06-06 03:30:00   [False, False, False, True]        5.825800   
2022-06-06 03:45:00  [False, False, False, False]        6.199498   
2022-06-06 04:00:00  [False, False, False, False]        8.531354   
2022-06-06 04:15:00  [False, False, False, False]        8.821097   
2022-06-06 04:30:00   [False, True, False, False]        8.642420   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -2.394412e+00    15.000000  -27.25102   
2022-01-01 00:15:00                0.0  0.000000e+00    -4.070878    0.00000   
2022-01-01 00:30:00                0.0 -3.442527e+00    -3.733359    0.00000   
2022-01-01 00:45:00                0.0 -3.240015e+00    -6.966519    0.00000   
2022-01-01 01:00:00                0.0 -6.163171e+00    -5.901051    0.00000   
...                                ...           ...          ...        ...   
2022-06-06 03:30:00               -2.0 -4.440892e-16    15.000000    0.00000   
2022-06-06 03:45:00               -2.0  0.000000e+00    15.000000    0.00000   
2022-06-06 04:00:00               -2.0  0.000000e+00    15.000000    0.00000   
2022-06-06 04:15:00               -2.0  0.000000e+00    15.000000    0.00000   
2022-06-06 04:30:00               -2.0  8.881784e-16    15.000000    0.00000   

                       rewards  
time                            
2022-01-01 00:00:00 -12.251020  
2022-01-01 00:15:00  -4.070878  
2022-01-01 00:30:00  -3.733359  
2022-01-01 00:45:00  -6.966519  
2022-01-01 01:00:00  -5.901051  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00

In [58]:
env.plot_VPP_autarky()

In [59]:
#env.plot_VPP_results()

In [60]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [61]:
env.plot_VPP_Elvis_comparison()

In [62]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [63]:
env.plot_rewards_stats()

In [64]:
env.plot_EVs_kpi()

In [65]:
env.plot_actions_kpi()

In [66]:
env.plot_load_kpi()

In [67]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [68]:
#env.close()